## 3. Cluster-preparation and graph generation

Preparation for clustering(we convert the itemsets of shingles/keywords/descriptors and calculate a
similarity measure between each itemsets -> this in turn forms a fully connected
graph(edges == similarity, nodes == games) which we can then prune by removing the edges where
the weight is below a threshold)

### imports

In [2]:
import polars as pl
import numpy as np
import h5py

import itertools
from pathlib import Path
from collections import defaultdict
import re
import random


DATA = Path('./data')

GEN_DATA = DATA / "gen"
RAW_DATA = DATA / "raw"



### loading data

In [ ]:
from statistics import mean

df = pl.read_csv(RAW_DATA / 'games_detailed_info2025.csv')

df

shape: (27_780, 52)
┌───────┬───────────┬────────┬─────────────┬───┬────────────┬────────────┬────────────┬────────────┐
│       ┆ type      ┆ id     ┆ thumbnail   ┆ … ┆ Children's ┆ RPG Item   ┆ Accessory  ┆ name       │
│ ---   ┆ ---       ┆ ---    ┆ ---         ┆   ┆ Game Rank  ┆ Rank       ┆ Rank       ┆ ---        │
│ i64   ┆ str       ┆ i64    ┆ str         ┆   ┆ ---        ┆ ---        ┆ ---        ┆ str        │
│       ┆           ┆        ┆             ┆   ┆ str        ┆ str        ┆ str        ┆            │
╞═══════╪═══════════╪════════╪═════════════╪═══╪════════════╪════════════╪════════════╪════════════╡
│ 0     ┆ boardgame ┆ 13     ┆ https://cf. ┆ … ┆ null       ┆ null       ┆ null       ┆ CATAN      │
│       ┆           ┆        ┆ geekdo-imag ┆   ┆            ┆            ┆            ┆            │
│       ┆           ┆        ┆ es.com/P…   ┆   ┆            ┆            ┆            ┆            │
│ 1     ┆ boardgame ┆ 822    ┆ https://cf. ┆ … ┆ null       ┆ null       ┆ null       ┆ Carcassonn │
│       ┆           ┆        ┆ geekdo-imag ┆   ┆            ┆            ┆            ┆ e          │
│       ┆           ┆        ┆ es.com/o…   ┆   ┆            ┆            ┆            ┆            │
│ 2     ┆ boardgame ┆ 30549  ┆ https://cf. ┆ … ┆ null       ┆ null       ┆ null       ┆ Pandemic   │
│       ┆           ┆        ┆ geekdo-imag ┆   ┆            ┆            ┆            ┆            │
│       ┆           ┆        ┆ es.com/S…   ┆   ┆            ┆            ┆            ┆            │
│ 3     ┆ boardgame ┆ 68448  ┆ https://cf. ┆ … ┆ null       ┆ null       ┆ null       ┆ 7 Wonders  │
│       ┆           ┆        ┆ geekdo-imag ┆   ┆            ┆            ┆            ┆            │
│       ┆           ┆        ┆ es.com/3…   ┆   ┆            ┆            ┆            ┆            │
│ 4     ┆ boardgame ┆ 167791 ┆ https://cf. ┆ … ┆ null       ┆ null       ┆ null       ┆ Terraformi │
│       ┆           ┆        ┆ geekdo-imag ┆   ┆            ┆            ┆            ┆ ng Mars    │
│       ┆           ┆        ┆ es.com/w…   ┆   ┆            ┆            ┆            ┆            │
│ …     ┆ …         ┆ …      ┆ …           ┆ … ┆ …          ┆ …          ┆ …          ┆ …          │
│ 27775 ┆ boardgame ┆ 420914 ┆ https://cf. ┆ … ┆ null       ┆ null       ┆ null       ┆ Iliad      │
│       ┆           ┆        ┆ geekdo-imag ┆   ┆            ┆            ┆            ┆            │
│       ┆           ┆        ┆ es.com/V…   ┆   ┆            ┆            ┆            ┆            │
│ 27776 ┆ boardgame ┆ 315131 ┆ https://cf. ┆ … ┆ null       ┆ null       ┆ null       ┆ Dumb       │
│       ┆           ┆        ┆ geekdo-imag ┆   ┆            ┆            ┆            ┆ Criminals  │
│       ┆           ┆        ┆ es.com/x…   ┆   ┆            ┆            ┆            ┆            │
│ 27777 ┆ boardgame ┆ 184452 ┆ https://cf. ┆ … ┆ null       ┆ null       ┆ null       ┆ Avarium    │
│       ┆           ┆        ┆ geekdo-imag ┆   ┆            ┆            ┆            ┆ Academy    │
│       ┆           ┆        ┆ es.com/9…   ┆   ┆            ┆            ┆            ┆            │
│ 27778 ┆ boardgame ┆ 197693 ┆ https://cf. ┆ … ┆ null       ┆ null       ┆ null       ┆ Cheeky     │
│       ┆           ┆        ┆ geekdo-imag ┆   ┆            ┆            ┆            ┆ Monkeys    │
│       ┆           ┆        ┆ es.com/H…   ┆   ┆            ┆            ┆            ┆            │
│ 27779 ┆ boardgame ┆ 31858  ┆ https://cf. ┆ … ┆ null       ┆ null       ┆ null       ┆ Geominos   │
│       ┆           ┆        ┆ geekdo-imag ┆   ┆            ┆            ┆            ┆            │
│       ┆           ┆        ┆ es.com/W…   ┆   ┆            ┆            ┆            ┆            │
└───────┴───────────┴────────┴─────────────┴───┴────────────┴────────────┴────────────┴────────────┘

In [ ]:
desc = df["description"].fill_null("")

mean(map(len, desc))

In [6]:
data = list(zip(df["id"], df["description"]))
data

[(13,
  "In CATAN (formerly The Settlers of Catan), players try to be the dominant force on the island of Catan by building settlements, cities and roads. On each turn dice are rolled to determine which resources the island produces. Players build structures by 'spending' resources (sheep, wheat, wood, brick and ore) which are represented by the relevant resource cards; each land type, with the exception of the unproductive desert, produces a specific resource: hills produce brick, forests produce wood, mountains produce ore, fields produce wheat, and pastures produce sheep.&#10;&#10;Set-up includes randomly placing large hexagonal tiles (each depicting one of the five resource-producing terrain types--or the desert) in a honeycomb shape and surrounding them with water tiles, some of which contain ports of exchange. A number disk, the value of which will correspond to the roll of two 6-sided dice, are placed on each terrain tile. Each player is given two settlements (think: houses) and

#### Shingling

For each game, convert its description into a set of hashed shingles.

1. Preprocessing
2. Shingles (n-grams)
3. Hashing


In [ ]:
import re
import xxhash
import string

STOPWORDS = {
    "the","a","an","and","of","to","in","for","on","with","by","at","from",
    "this","that","these","those","players","player","play","game","games"
}

TRANS = {ord(c): ' ' for c in string.punctuation if c != '-'}
TRANS.update({ord(c): ' ' for c in string.ascii_uppercase})

def preprocess(text):
    if not text:
        return []
    text = text.lower().translate(TRANS)
    tokens = text.split()
    return [t for t in tokens if t not in STOPWORDS]

def shingle_hash(s):
    return xxhash.xxh64(s).intdigest()

def shingles_for_one(gid, desc, n=3):
    tokens = preprocess(desc)
    out = set()
    limit = len(tokens) - n + 1

    for i in range(limit):
        s = tokens[i] + " " + tokens[i+1] + " " + tokens[i+2]
        out.add(shingle_hash(s))

    return out

def shingle_all(df, n=3):
    shingle_dict = {}
    ids = df["id"]
    descs = df["description"]

    for gid, desc in zip(ids, descs):
        shingle_dict[gid] = shingles_for_one(gid, desc, n)

    return shingle_dict


In [ ]:
shingle_dict = shingle_all(df, n=3)


{13: {15908114453770950,
  76994805667385821,
  85293429607914688,
  177853532462229797,
  191428165850553278,
  244090316044818618,
  310498543047918766,
  599950294940965292,
  635673191131235801,
  685254717745734004,
  823785358343121597,
  825694184876980995,
  843486724434154402,
  844060522475381275,
  860661779700191434,
  883813927029978803,
  964962341531216238,
  1048114482587639268,
  1165783669232412821,
  1266198088826797511,
  1312489293752009666,
  1449020929162411892,
  1457782695734100873,
  1480922094452145382,
  1637735042283036675,
  1851734758802378885,
  1876014583130866853,
  1883551693874174579,
  1953789651869644628,
  1965965886016340203,
  2005358937240278478,
  2027716560230163454,
  2239887528547192437,
  2366545238650869540,
  2452261427348633858,
  2526699635233485333,
  2631955129637886208,
  2892099348896568674,
  2938992289827583185,
  2975566386755571375,
  2988002413554058951,
  3217498518216734799,
  3243306623530692380,
  3243664831954526704,
  34

In [36]:

print("Number of shingles per game:")
for g, s in shingle_dict.items():
    print(g, "->", len(s), "shingles")

Number of shingles per game:
13 -> 238 shingles
822 -> 156 shingles
30549 -> 193 shingles
68448 -> 201 shingles
167791 -> 305 shingles
266192 -> 116 shingles
173346 -> 218 shingles
230802 -> 98 shingles
178900 -> 158 shingles
36218 -> 222 shingles
9209 -> 171 shingles
169786 -> 278 shingles
148228 -> 175 shingles
14996 -> 152 shingles
31260 -> 240 shingles
40692 -> 197 shingles
70323 -> 158 shingles
3076 -> 314 shingles
129622 -> 114 shingles
163412 -> 298 shingles
39856 -> 144 shingles
2651 -> 174 shingles
84876 -> 331 shingles
174430 -> 188 shingles
199792 -> 196 shingles
110327 -> 136 shingles
28143 -> 332 shingles
478 -> 230 shingles
237182 -> 178 shingles
162886 -> 336 shingles
161936 -> 249 shingles
34635 -> 148 shingles
54043 -> 181 shingles
244521 -> 136 shingles
65244 -> 269 shingles
183394 -> 184 shingles
1927 -> 394 shingles
316554 -> 256 shingles
224517 -> 184 shingles
12333 -> 278 shingles
98778 -> 131 shingles
204583 -> 100 shingles
342942 -> 148 shingles
120677 -> 228 sh

### MinHash

Compress the large shingle set for each game into a small signature vector.

- Choose `k` hash functions:  
  `h_i(x) = (a_i * x + b_i) mod P`, with random `a_i`, `b_i`, and a large prime `P`.

- For each game and each hash function:
  - Apply hash function to each shingle in the game's set.
  - Take the minimum hashed value. This is the MinHash component for that hash function.


In [15]:
import numpy as np
import random

def build_minhash_functions(k, P=(1 << 61) - 1, seed=42):
    random.seed(seed)
    A = np.array([random.randint(1, P-1) for _ in range(k)], dtype=np.uint64)
    B = np.array([random.randint(0, P-1) for _ in range(k)], dtype=np.uint64)
    return A, B, np.uint64(P)

def minhash_signature(shingles, A, B, P):
    if not shingles:
        return np.full(len(A), P, dtype=np.uint64)

    x = np.fromiter(shingles, dtype=np.uint64)
    vals = (A[None, :] * x[:, None] + B[None, :]) % P
    return vals.min(axis=0)


In [17]:
def build_all_signatures(shingle_dict, k):
    A, B, P = build_minhash_functions(k)
    sigs = {}
    for gid, shs in shingle_dict.items():
        sigs[gid] = minhash_signature(shs, A, B, P)
    return sigs

In [49]:
sigs = build_all_signatures(shingle_dict, k=128)

In [50]:
print("signatures:", len(sigs), "length:", len(next(iter(sigs.values()))))

signatures: 27780 length: 128


#### Locality-Sensitive Hashing with banding

We use the classic MMDS banding technique:

- Signature length: `k`
- Choose number of bands `B` and rows per band `R` so that `B * R = k`
- For each game and each band:
  - Extract the band (a slice of the signature vector).
  - Hash the band to a bucket id.
  - Games whose bands hash to the same bucket are "candidates" to be similar.


In [ ]:
def lsh_candidates(sigs, B=16):
    game_ids = list(sigs.keys())
    N = len(game_ids)
    k = len(next(iter(sigs.values())))
    R = k // B
    assert B * R == k, "k must be divisible by B"

    buckets = {}
    for gid, sig in sigs.items():
        for b in range(B):
            start = b * R
            band = tuple(sig[start:start+R])
            h = hash((b, band)) 
            if h not in buckets:
                buckets[h] = []
            buckets[h].append(gid)

    #Generate pairs
    pairs = set()
    for bucket_id, ids in buckets.items():
        if len(ids) < 2:
            continue
        ids = sorted(ids)
        for i in range(len(ids)):
            for j in range(i+1, len(ids)):
                pairs.add((ids[i], ids[j]))

    return pairs


In [ ]:
lsh = lsh_candidates(sigs)
id_to_title = dict(zip(df["id"], df["name"]))


pairs_named = list(map(
    lambda ab: f"{id_to_title[ab[0]]} <-> {id_to_title[ab[1]]}",
    lsh
))

pairs_named


['Funkoverse Strategy Game: DC Comics 100 -> Funkoverse Strategy Game: Harry Potter 102',
 'Excalibohn -> Bohnanza: 25th Anniversary Edition',
 "Funkoverse Strategy Game: Tim Burton's The Nightmare Before Christmas 100 -> Funkoverse Strategy Game: Game of Thrones 100",
 'Anno Domini: Frauen -> Anno Domini: Sex & Crime',
 "Funkoverse Strategy Game: Tim Burton's The Nightmare Before Christmas 100 -> Funkoverse Strategy Game: Harry Potter 102",
 'Exceed: Red Horizon – Reese, Heidi, Nehtali, and Vincent -> Exceed: Red Horizon – Satoshi, Mei Lien, Morathi, and Baelkhor',
 'For What Remains: Streets of Ruin -> For What Remains: Out of the Basement',
 'Animal Upon Animal: Dinos -> Animal Upon Animal: Unicorns',
 'Eleminis -> Superbohaterowie',
 "Funkoverse Strategy Game: Tim Burton's The Nightmare Before Christmas 100 -> Funkoverse Strategy Game: Marvel 100",
 'Marvel United -> Marvel United: Multiverse',
 'Q.E. -> QE',
 'Anno Domini: Kirche & Staat -> Anno Domini: Showbizz',
 "Rory's Story C

In [60]:
def jaccard(A, B):
    inter = len(A & B)
    union = len(A | B)
    return inter / union if union > 0 else 0.0


def exact_jaccard_for_candidates(shingle_dict, candidates):
    out = []
    for a, b in candidates:
        s = jaccard(shingle_dict[a], shingle_dict[b])
        out.append((a, b, s))
    return out


In [64]:
jac_pairs = exact_jaccard_for_candidates(shingle_dict, lsh)
jac_pairs

used_ids = set()

for a, b in lsh:
    used_ids.add(a)
    used_ids.add(b)

print("Number of games in candidate graph:", len(used_ids))

Number of games in candidate graph: 593


In [ ]:
game_ids = sorted(list(used_ids))
id_to_index = {gid: i for i, gid in enumerate(game_ids)}
N = len(game_ids)

S = np.zeros((N, N), dtype=np.float32)

for a, b in lsh:
    i = id_to_index[a]
    j = id_to_index[b]
    sim = jaccard(shingle_dict[a], shingle_dict[b])
    S[i, j] = sim
    S[j, i] = sim

np.fill_diagonal(S, 0.0)   # INFO -> TECHNICALLY SHOULD BE 1, but does not work for my tool

game_titles = [id_to_title[g] for g in game_ids]

with h5py.File(GEN_DATA / "gam_sim_small.h5", "w") as f:
    f.create_dataset("matrix", data=S.astype(np.float32))
    f.create_dataset(
        "node_names",
        data=np.array(game_titles, dtype=h5py.string_dtype())
    )

## full minhash Matrix

In [ ]:
import numpy as np

def full_minhash_matrix(sigs):
    keys = list(sigs.keys())
    N = len(keys)
    k = len(next(iter(sigs.values())))

    M = np.vstack([sigs[g] for g in keys])
    M = M.astype(np.uint64)
    print(M[:5])
    print(np.unique(M, axis=0).shape)
    S = np.zeros((N, N), dtype=np.float16)

    for i in range(N):
        eq = (M[i] == M[i+1:])
        sims = eq.mean(axis=1)
        S[i, i+1:] = sims
        S[i+1:, i] = sims

    np.fill_diagonal(S, 0) # technically it should be 1 but my tool is not working this way

    return keys, S


In [ ]:
keys, SimilarityMatrix = full_minhash_matrix(sigs)

[[ 3510647397620425 15338983258644953  7121995958837106  9483587277079722
    113977077123849  2190669154861003 11626462023664658 13105635881063912
   4634925473994094  1795389916085611 11525273361811017  8149096543236479
   9297580216126661   628589923125487 17570903418896675   346469655300010
  30400694812124856  9395723247218144 14223009524313266  8138787345863659
    394034068379750  1587556536437164   126852099975916 10833595465114953
   2454622990788730 14039434445375588 17414770053555338   976112978663943
   6307150951703703 11406981646731525 19663037786490903   579512014608430
  12449599587530736   327818502420497  7247187925052831  7254894975403354
  22870273132020692  1313551037341979 26359733149581328  2691764095437160
   1118969214147179 15249378676166682  1296968529179661 10287122855389214
   5025901818632699 12753923639347110 13360574926194444 13758426534107462
  27659635138229980 10193612615026775  5942926913065043 12040114483020204
   5308562782580048 23379604592965645 

In [ ]:
print("SimilarityMatrix min/max:", SimilarityMatrix.min(), SimilarityMatrix.max())


S min/max: 0.0 1.0


### Storing as my format 
for use in gxpvis.skumantz.dev

In [45]:
id_to_title = dict(zip(df["id"], df["name"]))
game_titles = [id_to_title[g] for g in keys]


In [ ]:

with h5py.File(GEN_DATA / "game_similarity.h5", "w") as f:
    f.create_dataset("matrix", data=SimilarityMatrix)
    f.create_dataset("node_names", data=np.array(game_titles, dtype=h5py.string_dtype()))



### NLP part

In [75]:
import numpy as np
from sentence_transformers import SentenceTransformer

descriptions = df["description"].fill_null("").to_list()

model = SentenceTransformer("all-MiniLM-L6-v2")


emb = model.encode(
    descriptions,
    convert_to_numpy=True,
    normalize_embeddings=True,
    show_progress_bar=True
)


sim_cosine = emb @ emb.T 

#sim_cosine = sim_cosine.astype(np.float32)
game_titles = df["name"].to_list()

Xet Storage is enabled for this repo, but the 'hf_xet' package is not installed. Falling back to regular HTTP download. For better performance, install the package with: `pip install huggingface_hub[hf_xet]` or `pip install hf_xet`
Batches: 100%|██████████| 869/869 [08:57<00:00,  1.62it/s]


In [77]:
max_sim = sim_cosine.max(axis=1)
mean_sim = (sim_cosine.sum(axis=1) - 1.0) / (sim_cosine.shape[1]-1)
threshold = 0.3
degree = (sim_cosine > threshold).sum(axis=1)
score = 0.5*max_sim + 0.3*mean_sim + 0.2*(degree / degree.max())
N = 1000 
idx = np.argsort(score)[-N:]


sim_small = sim_cosine[idx][:, idx]
titles_small = np.array(game_titles)[idx]


In [78]:

with h5py.File(GEN_DATA / "game_similarity_transformer_small.h5", "w") as f:
    f.create_dataset("matrix", data=sim_small)
    f.create_dataset(
        "node_names",
        data=np.array(titles_small, dtype=h5py.string_dtype())
    )